Compute EF-SM models
--

In [2]:
import sys
import os
import argparse
import numpy as np
import pandas as pd
import xarray as xr
import itertools

from global_land_mask import is_land

from config import KSCALEOUTDIR
from landatmospherecoupling import LACR
from read_data import *
from p_config import regions

In [3]:
season='winter'
driving='GAL9'
res_glo = 'n1280'
phy_glo = 'GAL9'
res_cha='km4p4'
res_lam='km2p2'
region='africa'
physics='RAL3'
depth=0  # soil layer [0, 3]

year = 2020
dates = {2: np.arange(1, 28+1, 1)}   # 1: np.arange(20, 30+1, 1)

lat_range = regions[region][0]
lon_range = regions[region][1]

lat_range = (-15., 5.)
lon_range = (-10., 40.)

lat_min = lat_range[0]
lat_max = lat_range[1]
lon_min = lon_range[0]
lon_max = lon_range[1]

In [4]:
#~ Outdir

if season == 'summer':
    path_season = 'outdir_20160801T0000Z'
elif season == 'winter':
    path_season = 'outdir_20200120T0000Z'

if not os.path.isdir(KSCALEOUTDIR + '/' + path_season):
    os.mkdir(KSCALEOUTDIR + '/' + path_season)
outdir = KSCALEOUTDIR + '/' + path_season

if not os.path.isdir(outdir + '/ef_sm'):
    os.mkdir(outdir + '/ef_sm')
outdir = outdir + '/ef_sm'

if not os.path.isdir(outdir + '/DMn1280' + driving):
    os.mkdir(outdir + '/DMn1280' + driving)
outdir = outdir + '/DMn1280' + driving

if not os.path.isdir(outdir + '/global_' + res_glo + '_' + phy_glo):
    os.mkdir(outdir + '/global_' + res_glo + '_' + phy_glo)
outdir_glo = outdir + '/global_' + res_glo + '_' + phy_glo

if not os.path.isdir(outdir + '/channel_' + res_cha + '_' + physics):
    os.mkdir(outdir + '/channel_' + res_cha + '_' + physics)
outdir_cha = outdir + '/channel_' + res_cha + '_' + physics

if not os.path.isdir(outdir + '/lam_' + res_lam + '_' + physics):
    os.mkdir(outdir + '/lam_' + res_lam + '_' + physics)
outdir_lam = outdir + '/lam_' + res_lam + '_' + physics


print('Output directories:\n%s \n%s \n%s'%(outdir_glo, outdir_cha, outdir_lam))

Output directories:
/home/users/guicha/Pythons/KSCALE/outputs/data/outdir_20200120T0000Z/ef_sm/DMn1280GAL9/global_n1280_GAL9 
/home/users/guicha/Pythons/KSCALE/outputs/data/outdir_20200120T0000Z/ef_sm/DMn1280GAL9/channel_km4p4_RAL3 
/home/users/guicha/Pythons/KSCALE/outputs/data/outdir_20200120T0000Z/ef_sm/DMn1280GAL9/lam_km2p2_RAL3


In [5]:
#~ Get data

sms_glo = []
sms_cha = []
sms_lam = []

efs_glo = load_var_global(season, driving, res_glo, phy_glo, 'ef', (lat_min, lat_max), (lon_min, lon_max))
efs_cha = load_var_channel(season, driving, res_cha, physics, 'ef', (lat_min, lat_max), (lon_min, lon_max))
efs_lam = load_var_lam(season, driving, region, res_lam, physics, 'ef', (lat_min, lat_max), (lon_min, lon_max))

for month, days in dates.items():
    print('\no %i'%month)
    for day in days:
        print(day, end=' : ', flush=True)

        sm_glo = load_data_global_smc(season, driving, res_glo, phy_glo, year, month, day, (lat_min, lat_max), (lon_min, lon_max), depth)
        sm_cha = load_data_channel_smc(season, driving, res_cha, physics, year, month, day, (lat_min, lat_max), (lon_min, lon_max), depth)
        sm_lam = load_data_lam_smc(season, driving, region, 'km4p4', physics, year, month, day, (lat_min, lat_max), (lon_min, lon_max), depth)

        sms_glo.append(sm_glo)
        sms_cha.append(sm_cha)
        sms_lam.append(sm_lam)

sms_glo = xr.concat(sms_glo, dim='time')
sms_cha = xr.concat(sms_cha, dim='time')
sms_lam = xr.concat(sms_lam, dim='time')

sms_glo = sms_glo.resample(time='1d').mean()
sms_cha = sms_cha.resample(time='1d').mean()
sms_lam = sms_lam.resample(time='1d').mean()


o 2
1 : 2 : 3 : 4 : 5 : 6 : 7 : 8 : 9 : 10 : 11 : 12 : 13 : 14 : 15 : 16 : 17 : 18 : 19 : 20 : 21 : 22 : 23 : 24 : 25 : 26 : 27 : 28 : 

In [6]:
# Get 3-month subsets
#imths = efs_glo.groupby('time.month').groups
#lmonths = [imths[m] for m in months]
#lmonths = list(itertools.chain(*lmonths))

lats = efs_glo.latitude.values
lons = efs_glo.longitude.values

In [8]:
#~ Get LACR models

out_nums_glo = xr.DataArray(data=None, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_wilts_glo = xr.DataArray(data=None, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_crits_glo = xr.DataArray(data=None, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_slopes_glo = xr.DataArray(data=None, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_t_trans_glo = xr.DataArray(data=None, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))

out_nums_cha = xr.DataArray(data=None, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_wilts_cha = xr.DataArray(data=None, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_crits_cha = xr.DataArray(data=None, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_slopes_cha = xr.DataArray(data=None, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_t_trans_cha = xr.DataArray(data=None, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))

out_nums_lam = xr.DataArray(data=None, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_wilts_lam = xr.DataArray(data=None, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_crits_lam = xr.DataArray(data=None, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_slopes_lam = xr.DataArray(data=None, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_t_trans_lam = xr.DataArray(data=None, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))

out_nums_glo = []
out_nums_cha = []
out_nums_lam = []
out_wilt_glo = []
out_wilt_cha = []
out_wilt_lam = []
out_crit_glo = []
out_crit_cha = []
out_crit_lam = []
out_slop_glo = []
out_slop_cha = []
out_slop_lam = []
out_time_glo = []
out_time_cha = []
out_time_lam = []

for ilat, lat in enumerate(lats):
    print('\n>>> {0} <<<'.format(lat))

    out_nums_glo_ = []
    out_nums_cha_ = []
    out_nums_lam_ = []
    out_wilt_glo_ = []
    out_wilt_cha_ = []
    out_wilt_lam_ = []
    out_crit_glo_ = []
    out_crit_cha_ = []
    out_crit_lam_ = []
    out_slop_glo_ = []
    out_slop_cha_ = []
    out_slop_lam_ = []
    out_time_glo_ = []
    out_time_cha_ = []
    out_time_lam_ = []

    for ilon, lon in enumerate(lons):
        if (is_land(lat, lon)):  # and (np.isnan(efs_glo_pt.values).all() != True) and (np.isnan(sms_glo_pt.values).all() != True):
            efs_glo_pt = efs_glo.sel(latitude=lat, longitude=lon, method='nearest')
            sms_glo_pt = sms_glo.sel(latitude=lat, longitude=lon, method='nearest')
            efs_cha_pt = efs_cha.sel(latitude=lat, longitude=lon, method='nearest')
            sms_cha_pt = sms_cha.sel(latitude=lat, longitude=lon, method='nearest')
            efs_lam_pt = efs_lam.sel(latitude=lat, longitude=lon, method='nearest')
            sms_lam_pt = sms_lam.sel(latitude=lat, longitude=lon, method='nearest')

            df_glo = pd.DataFrame(data={'sm': sms_glo_pt, 'ef': efs_glo_pt})
            df_glo = df_glo.dropna(axis=0, how='any')
            df_glo = df_glo.sort_values('sm')

            df_cha = pd.DataFrame(data={'sm': sms_cha_pt, 'ef': efs_cha_pt})
            df_cha = df_cha.dropna(axis=0, how='any')
            df_cha = df_cha.sort_values('sm')

            df_lam = pd.DataFrame(data={'sm': sms_lam_pt, 'ef': efs_lam_pt})
            df_lam = df_lam.dropna(axis=0, how='any')
            df_lam = df_lam.sort_values('sm')

            if (len(df_glo) >= 10) and (len(df_cha) >= 10) and (len(df_lam) >= 10) and (df_glo.sm.std()!=0) and (df_cha.sm.std()!=0) and (df_lam.sm.std()!=0) and (df_glo.sm.mean()>1.5) and (df_cha.sm.mean()>1.5) and (df_lam.sm.mean()!=1.5):
                models_glo = LACR(df_glo.sm.values, df_glo.ef.values)
                models_cha = LACR(df_cha.sm.values, df_cha.ef.values)
                models_lam = LACR(df_lam.sm.values, df_lam.ef.values)

                out_nums_glo_.append(models_glo.get_best_model_number())
                out_nums_cha_.append(models_cha.get_best_model_number())
                out_nums_lam_.append(models_lam.get_best_model_number())

                out_wilt_glo_.append(models_glo.get_wilting_point())
                out_wilt_cha_.append(models_cha.get_wilting_point())
                out_wilt_lam_.append(models_lam.get_wilting_point())

                out_crit_glo_.append(models_glo.get_critical_point())
                out_crit_cha_.append(models_cha.get_critical_point())
                out_crit_lam_.append(models_lam.get_critical_point())

                out_slop_glo_.append(models_glo.get_slope())
                out_slop_cha_.append(models_cha.get_slope())
                out_slop_lam_.append(models_lam.get_slope())

                out_time_glo_.append(models_glo.get_transitional_time_frac())
                out_time_cha_.append(models_cha.get_transitional_time_frac())
                out_time_lam_.append(models_lam.get_transitional_time_frac())
            else:
                out_nums_glo_.append(np.nan)
                out_nums_cha_.append(np.nan)
                out_nums_lam_.append(np.nan)
                out_wilt_glo_.append(np.nan)
                out_wilt_cha_.append(np.nan)
                out_wilt_lam_.append(np.nan)
                out_crit_glo_.append(np.nan)
                out_crit_cha_.append(np.nan)
                out_crit_lam_.append(np.nan)
                out_slop_glo_.append(np.nan)
                out_slop_cha_.append(np.nan)
                out_slop_lam_.append(np.nan)
                out_time_glo_.append(np.nan)
                out_time_cha_.append(np.nan)
                out_time_lam_.append(np.nan)
                #sys.exit()
        else:
            out_nums_glo_.append(np.nan)
            out_nums_cha_.append(np.nan)
            out_nums_lam_.append(np.nan)
            out_wilt_glo_.append(np.nan)
            out_wilt_cha_.append(np.nan)
            out_wilt_lam_.append(np.nan)
            out_crit_glo_.append(np.nan)
            out_crit_cha_.append(np.nan)
            out_crit_lam_.append(np.nan)
            out_slop_glo_.append(np.nan)
            out_slop_cha_.append(np.nan)
            out_slop_lam_.append(np.nan)
            out_time_glo_.append(np.nan)
            out_time_cha_.append(np.nan)
            out_time_lam_.append(np.nan)

    out_nums_glo.append(out_nums_glo_)
    out_nums_cha.append(out_nums_cha_)
    out_nums_lam.append(out_nums_lam_)
    out_wilt_glo.append(out_wilt_glo_)
    out_wilt_cha.append(out_wilt_cha_)
    out_wilt_lam.append(out_wilt_lam_)
    out_crit_glo.append(out_crit_glo_)
    out_crit_cha.append(out_crit_cha_)
    out_crit_lam.append(out_crit_lam_)
    out_slop_glo.append(out_slop_glo_)
    out_slop_cha.append(out_slop_cha_)
    out_slop_lam.append(out_slop_lam_)
    out_time_glo.append(out_time_glo_)
    out_time_cha.append(out_time_cha_)
    out_time_lam.append(out_time_lam_)

out_nums_glo = np.asarray(out_nums_glo)
out_nums_cha = np.asarray(out_nums_cha)
out_nums_lam = np.asarray(out_nums_lam)
out_wilt_glo = np.asarray(out_wilt_glo)
out_wilt_cha = np.asarray(out_wilt_cha)
out_wilt_lam = np.asarray(out_wilt_lam)
out_crit_glo = np.asarray(out_crit_glo)
out_crit_cha = np.asarray(out_crit_cha)
out_crit_lam = np.asarray(out_crit_lam)
out_slop_glo = np.asarray(out_slop_glo)
out_slop_cha = np.asarray(out_slop_cha)
out_slop_lam = np.asarray(out_slop_lam)
out_time_glo = np.asarray(out_time_glo)
out_time_cha = np.asarray(out_time_cha)
out_time_lam = np.asarray(out_time_lam)

out_nums_glo_da = xr.DataArray(data=out_nums_glo, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_nums_cha_da = xr.DataArray(data=out_nums_cha, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_nums_lam_da = xr.DataArray(data=out_nums_lam, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_wilt_glo_da = xr.DataArray(data=out_wilt_glo, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_wilt_cha_da = xr.DataArray(data=out_wilt_cha, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_wilt_lam_da = xr.DataArray(data=out_wilt_lam, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_crit_glo_da = xr.DataArray(data=out_crit_glo, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_crit_cha_da = xr.DataArray(data=out_crit_cha, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_crit_lam_da = xr.DataArray(data=out_crit_lam, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_slop_glo_da = xr.DataArray(data=out_slop_glo, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_slop_cha_da = xr.DataArray(data=out_slop_cha, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_slop_lam_da = xr.DataArray(data=out_slop_lam, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_time_glo_da = xr.DataArray(data=out_time_glo, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_time_cha_da = xr.DataArray(data=out_time_cha, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))
out_time_lam_da = xr.DataArray(data=out_time_lam, dims=['latitude', 'longitude'], coords=dict(latitude=(['latitude'], lats), longitude=(['longitude'], lons)))


>>> -14.949999809265137 <<<


/home/users/guicha/conda/envs/kscale/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:1010: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',
/home/users/guicha/conda/envs/kscale/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:1010: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',
/home/users/guicha/conda/envs/kscale/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:1010: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',
/home/users/guicha/conda/envs/kscale/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:1010: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',
/home/users/guicha/conda/envs/ks


>>> -14.850000381469727 <<<


/home/users/guicha/conda/envs/kscale/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:1010: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',
/home/users/guicha/conda/envs/kscale/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:1010: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',
/home/users/guicha/conda/envs/kscale/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:1010: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',
/home/users/guicha/conda/envs/kscale/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:1010: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',
/home/users/guicha/conda/envs/ks


>>> -14.75 <<<


...

/home/users/guicha/conda/envs/kscale/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:1010: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',
/home/users/guicha/conda/envs/kscale/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:1010: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',
/home/users/guicha/conda/envs/kscale/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:1010: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',
/home/users/guicha/conda/envs/kscale/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:1010: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',
/home/users/guicha/conda/envs/ks


>>> 4.849999904632568 <<<


/home/users/guicha/conda/envs/kscale/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:1010: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',
/home/users/guicha/conda/envs/kscale/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:1010: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',
/home/users/guicha/conda/envs/kscale/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:1010: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',
/home/users/guicha/conda/envs/kscale/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:1010: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',
/home/users/guicha/conda/envs/ks


>>> 4.949999809265137 <<<


/home/users/guicha/conda/envs/kscale/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:1010: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',
/home/users/guicha/conda/envs/kscale/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:1010: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',
/home/users/guicha/conda/envs/kscale/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:1010: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',
/home/users/guicha/conda/envs/kscale/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:1010: OptimizeWarning: Covariance of the parameters could not be estimated
  warnings.warn('Covariance of the parameters could not be estimated',
/home/users/guicha/conda/envs/ks

In [15]:
#~ Save

outfile_nums_glo = outdir_glo + '/ef_sm_model_number_level=' + str(depth) + '.nc'
out_nums_glo_da.to_netcdf(outfile_nums_glo)
outfile_wilt_glo = outdir_glo + '/wilting_point_level=' + str(depth) + '.nc'
out_wilt_glo_da.to_netcdf(outfile_wilt_glo)
outfile_crit_glo = outdir_glo + '/critical_point_level=' + str(depth) + '.nc'
out_crit_glo_da.to_netcdf(outfile_crit_glo)
outfile_slop_glo = outdir_glo + '/slope_level=' + str(depth) + '.nc'
out_slop_glo_da.to_netcdf(outfile_slop_glo)
outfile_time_glo = outdir_glo + '/time_trans_level=' + str(depth) + '.nc'
out_time_glo_da.to_netcdf(outfile_time_glo)

outfile_nums_cha = outdir_cha + '/ef_sm_model_number_level=' + str(depth) + '.nc'
out_nums_cha_da.to_netcdf(outfile_nums_cha)
outfile_wilt_cha = outdir_cha + '/wilting_point_level=' + str(depth) + '.nc'
out_wilt_cha_da.to_netcdf(outfile_wilt_cha)
outfile_crit_cha = outdir_cha + '/critical_point_level=' + str(depth) + '.nc'
out_crit_cha_da.to_netcdf(outfile_crit_cha)
outfile_slop_cha = outdir_cha + '/slope_level=' + str(depth) + '.nc'
out_slop_cha_da.to_netcdf(outfile_slop_cha)
outfile_time_cha = outdir_cha + '/time_trans_level=' + str(depth) + '.nc'
out_time_cha_da.to_netcdf(outfile_time_cha)

outfile_nums_lam = outdir_lam + '/ef_sm_model_number_level=' + str(depth) + '.nc'
out_nums_lam_da.to_netcdf(outfile_nums_lam)
outfile_wilt_lam = outdir_lam + '/wilting_point_level=' + str(depth) + '.nc'
out_wilt_lam_da.to_netcdf(outfile_wilt_lam)
outfile_crit_lam = outdir_lam + '/critical_point_level=' + str(depth) + '.nc'
out_crit_lam_da.to_netcdf(outfile_crit_lam)
outfile_slop_lam = outdir_lam + '/slope_level=' + str(depth) + '.nc'
out_slop_lam_da.to_netcdf(outfile_slop_lam)
outfile_time_lam = outdir_lam + '/time_trans_level=' + str(depth) + '.nc'
out_time_lam_da.to_netcdf(outfile_time_lam)